In [1]:
import csv
import os
import tqdm

import biosppy.signals.ecg as ecg
import biosppy
import neurokit2 as nk

import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import scipy as sp

from scipy.fftpack import fft
import scipy.fftpack as sf

import sys

sys.path.append("..")
from util import load_base_data


SAMPLING_RATE = 300.0
DATAPATH = "/Users/ericschreiber/dev/ETH/AML/Project_1/aml-2023/task2/data"

In [2]:
X_train, y_train, X_test = load_base_data()

In [3]:
freq_array = [
    0.46981001,
    0.94989355,
    1.34722766,
    1.92037653,
    2.45140581,
    3.58897684,
    5.61198292,
    7.85416366,
    11.77742192,
    19.56926069,
]


def sum_freq_bands_for_beat(heartbeat, n=10, freq_array=freq_array):
    fourier_specture = np.abs(fft(heartbeat))
    freqs = sf.fftfreq(len(fourier_specture), 1.0 / SAMPLING_RATE)
    fourier_specture = fourier_specture[freqs >= 0]
    freqs = freqs[freqs >= 0]

    # cut even more base on the freq_array
    fourier_specture = fourier_specture[freqs <= freq_array[-1]]
    freqs = freqs[freqs <= freq_array[-1]]

    # compute the sums of frequency bands
    sums = []
    sums.append(np.sum(fourier_specture[freqs <= freq_array[0]]))
    for i in range(len(freq_array) - 1):
        sum = np.sum(
            fourier_specture[
                np.logical_and(freqs > freq_array[i], freqs <= freq_array[i + 1])
            ]
        )
        sums.append(sum)

    return sums


def sum_freq_bands_for_signal(clean_signal):
    _, info = nk.ecg_peaks(ecg_cleaned=clean_signal, sampling_rate=SAMPLING_RATE)
    features = []
    n_peaks = 10
    rpeaks = info["ECG_R_Peaks"]
    beats = biosppy.signals.ecg.extract_heartbeats(
        signal=clean_signal, rpeaks=rpeaks, sampling_rate=SAMPLING_RATE
    )["templates"]
    n_beats = len(beats)
    for i in range(n_beats):
        features.append(np.array(sum_freq_bands_for_beat(beats[i], n_peaks)))
    features = list(np.array(features).T)
    return features


def create_features_from_signal(ecg_or_ftt):
    features = []
    for sig in ecg_or_ftt:
        if len(sig) > 0:
            mean = np.mean(sig)
            std = np.std(sig)
            median = np.median(sig)
            min = np.min(sig)
            max = np.max(sig)
            skew = sp.stats.skew(sig)
            kurtosis = sp.stats.kurtosis(sig)
            variation = sp.stats.variation(sig)
            iqr = sp.stats.iqr(sig)
            features += [mean, std, median, min, max, skew, kurtosis, variation, iqr]
        else:
            print("Problem with feature extraction: empty array")
            features += [0] * 90

    if len(features) != 90:
        print("Problem with feature extraction: wrong number of features")
        print(len(features))
        print(features)
        print(ecg_or_ftt)
        return [0] * 90
    return features

In [4]:
def signal_to_noise(ecg):
    try:
        mean = np.mean(ecg)
        std = np.std(ecg)
        db = 20 * np.log10(abs(mean / std))
    except:
        db = 0
    return [db]

In [5]:
def signal_over_70_percent(ecg, peaks):
    try:
        threshold = np.max(ecg) * 0.7
        over = np.sum(ecg > threshold)
        percent = over / len(ecg)
        percent_over_peaks = over / len(peaks)
    except:
        percent = 0
        percent_over_peaks = 0
    return [percent, percent_over_peaks]

In [6]:
def clean_input(ecg):
    #  filtered using a finite impulse response bandpass filter
    cleaned = nk.ecg_clean(ecg, sampling_rate=SAMPLING_RATE, method="biosppy")
    cleaned, was_inverted = nk.ecg_invert(cleaned, sampling_rate=300, show=False)
    _, info = nk.ecg_peaks(ecg_cleaned=cleaned, sampling_rate=SAMPLING_RATE)
    rpeaks = info["ECG_R_Peaks"]
    return cleaned, rpeaks

In [7]:
def make_features(ecg):
    cleaned, rpeaks = clean_input(ecg)
    features = []
    features += signal_to_noise(cleaned)
    features += signal_over_70_percent(cleaned, rpeaks)
    features += create_features_from_signal(sum_freq_bands_for_signal(cleaned))
    features = np.array(features).flatten()
    return features


def make_features_from_df(df):
    features = []
    for i in tqdm.tqdm(range(len(df))):
        ecg = df.iloc[i].values
        features.append(make_features(ecg))
    numpy = np.array(features)
    df = pd.DataFrame(numpy).reset_index(drop=False)
    df.drop(columns=["index"], inplace=True)
    df.index.name = "id"

    return df

In [8]:
features_X_train = make_features_from_df(X_train)

  0%|          | 0/5117 [00:00<?, ?it/s]

/Users/ericschreiber/miniconda3/envs/ml/lib/python3.10/site-packages/neurokit2/ecg/ecg_clean.py:101: NeuroKitWarning: There are 1485 missing data points in your signal. Filling missing values by using the forward filling method.
  warn(
/Users/ericschreiber/miniconda3/envs/ml/lib/python3.10/site-packages/neurokit2/ecg/ecg_clean.py:153: FutureWarning: DataFrame.pad/Series.pad is deprecated. Use DataFrame.ffill/Series.ffill instead
  ecg_signal = pd.DataFrame.pad(pd.Series(ecg_signal))
  0%|          | 1/5117 [00:00<14:12,  6.00it/s]/Users/ericschreiber/miniconda3/envs/ml/lib/python3.10/site-packages/neurokit2/ecg/ecg_clean.py:101: NeuroKitWarning: There are 9254 missing data points in your signal. Filling missing values by using the forward filling method.
  warn(
/Users/ericschreiber/miniconda3/envs/ml/lib/python3.10/site-packages/neurokit2/ecg/ecg_clean.py:153: FutureWarning: DataFrame.pad/Series.pad is deprecated. Use DataFrame.ffill/Series.ffill instead
  ecg_signal = pd.DataFrame.p

In [9]:
features_X_train
# problematic index: 3145

0         1         2            3            4            5   \
id                                                                            
0    -335.229755  0.005279  1.402985  2353.646677  1515.838617  2182.363339   
1    -345.295457  0.003201  1.583333  2835.472522  1866.464783  2484.352723   
2    -355.792019  0.005335  3.166667  4180.592963  6201.997276  2687.803699   
3    -368.829449  0.012692  3.228571  2219.122886  1889.932841  1629.444532   
4    -347.299886  0.005953  2.304348  1999.481748  1749.241996  1674.339877   
...          ...       ...       ...          ...          ...          ...   
5112 -345.101053  0.002527  1.875000  6623.964456  7520.560341  3374.588785   
5113 -367.614880  0.012860  7.156250  1358.133606   655.451365  1212.399228   
5114 -374.150327  0.004268  2.111111  3474.146775  2303.472745  3737.881280   
5115 -342.396156  0.006907  3.727273  1594.066816   908.211412  1502.528339   
5116 -353.987577  0.004661  1.844444  2077.450835  2172.151691  1464.955472   

              6             7         8          9   ...           83  \
id                                                   ...                
0      32.128618   8486.834529  1.813677   4.612442  ...  1542.591681   
1      86.892510   7104.144219  0.622049  -0.471964  ...  1449.647058   
2     563.571110  34898.596104  4.093334  17.201246  ...  1185.697882   
3      50.944998   8154.177652  1.177962   1.109966  ...  7470.912316   
4       6.642041   7331.879998  1.153354   1.011788  ...  1688.240042   
...          ...           ...       ...        ...  ...          ...   
5112  107.864935  31397.115189  1.902762   3.085690  ...  4260.216602   
5113  202.074693   2782.961758  0.493098  -0.424308  ...   788.100960   
5114    5.945924   9732.132308  0.431091  -0.135447  ...  1144.489608   
5115   57.188388   3398.930720  0.241095  -0.701109  ...   683.233783   
5116   57.710622   9432.184011  1.756968   2.547551  ...  2202.098750   

                84           85            86            87            88  \
id                                                                          
0      9623.984693   998.590997   9634.934218   7700.378687  11989.424055   
1      7774.071600  1081.338709   7819.386512   5340.360710   9844.006311   
2     21672.191201   739.237074  21650.383717  20405.117137  23517.641747   
3     27450.504616  5352.102629  26746.161271  16107.271396  38641.970251   
4     13389.381035  1462.101723  13408.020396   8765.460374  15882.735148   
...            ...          ...           ...           ...           ...   
5112  21927.379196  7231.295783  21239.920035   4832.272030  43586.406659   
5113   8732.862646   708.966080   8831.013793   7217.398369  10176.975000   
5114  20317.184094  1263.322484  20067.753786  18544.062395  24739.212327   
5115   7179.635504   609.750532   7109.443934   5831.004441   8365.561378   
5116  12659.998946  1798.848429  12902.762726   7650.653638  16199.826924   

            89        90        91           92  
id                                               
0     0.346371 -0.391518  0.103761  1186.150394  
1    -0.102049 -0.490808  0.139096  1479.144645  
2     0.514289 -0.050549  0.034110  1105.642793  
3     0.214572 -0.996827  0.194973  9176.694422  
4    -1.034543  1.534529  0.109199  1514.666740  
...        ...       ...       ...          ...  
5112  0.649096  2.210675  0.329784  4950.462561  
5113 -0.195893 -0.486943  0.081184   889.336158  
5114  1.321463  2.366278  0.062180  1450.512755  
5115  0.079223 -0.753815  0.084928   936.566267  
5116 -0.520302  0.456101  0.142089  2204.646412  

[5117 rows x 93 columns]

In [10]:
# How many infs
print(f"Number of infs: {np.sum(np.isinf(features_X_train), axis=0).sum()}")
# Which columns have infs
cols_with_infs = np.where(np.isinf(features_X_train))[1]
cols_with_infs_unique = np.unique(cols_with_infs)
print(f"Columns with infs: {len(cols_with_infs_unique)}")
print(
    f"biggest pos value except inf: {np.max(features_X_train[features_X_train != np.inf].max())}"
)
print(f"biggest neg value: {np.min(features_X_train).min()}")
biggest_pos = np.max(features_X_train[features_X_train != np.inf].max())
biggest_neg = np.min(features_X_train).min()
# Replace infs with biggest pos value
features_X_train[features_X_train == np.inf] = biggest_pos
# Replace -infs with biggest neg value
features_X_train[features_X_train == -np.inf] = biggest_neg

Number of infs: 110
Columns with infs: 1
biggest pos value except inf: 376367.392008195
biggest neg value: -inf


In [11]:
X_train_save_path = os.path.join(
    DATAPATH, "feature_extraction/spectral_analysis_X_train_features.csv"
)
features_X_train.to_csv(X_train_save_path, index=True)

# Test Data

In [12]:
test_features = make_features_from_df(X_test)

# How many infs
print(f"Number of infs: {np.sum(np.isinf(test_features), axis=0).sum()}")
# Which columns have infs
cols_with_infs = np.where(np.isinf(test_features))[1]
cols_with_infs_unique = np.unique(cols_with_infs)
print(f"Columns with infs: {len(cols_with_infs_unique)}")
print(
    f"biggest pos value except inf: {np.max(test_features[test_features != np.inf].max())}"
)
print(f"biggest neg value: {np.min(test_features).min()}")
biggest_pos = np.max(test_features[test_features != np.inf].max())
biggest_neg = np.min(test_features).min()
# Replace infs with biggest pos value
test_features[test_features == np.inf] = biggest_pos
# Replace -infs with biggest neg value
test_features[test_features == -np.inf] = biggest_neg

  0%|          | 0/3411 [00:00<?, ?it/s]/Users/ericschreiber/miniconda3/envs/ml/lib/python3.10/site-packages/neurokit2/ecg/ecg_clean.py:101: NeuroKitWarning: There are 9658 missing data points in your signal. Filling missing values by using the forward filling method.
  warn(
/Users/ericschreiber/miniconda3/envs/ml/lib/python3.10/site-packages/neurokit2/ecg/ecg_clean.py:153: FutureWarning: DataFrame.pad/Series.pad is deprecated. Use DataFrame.ffill/Series.ffill instead
  ecg_signal = pd.DataFrame.pad(pd.Series(ecg_signal))
  0%|          | 1/3411 [00:00<16:15,  3.50it/s]/Users/ericschreiber/miniconda3/envs/ml/lib/python3.10/site-packages/neurokit2/ecg/ecg_clean.py:101: NeuroKitWarning: There are 11998 missing data points in your signal. Filling missing values by using the forward filling method.
  warn(
/Users/ericschreiber/miniconda3/envs/ml/lib/python3.10/site-packages/neurokit2/ecg/ecg_clean.py:153: FutureWarning: DataFrame.pad/Series.pad is deprecated. Use DataFrame.ffill/Series.ff

Number of infs: 53
Columns with infs: 1
biggest pos value except inf: 298680.6615015765
biggest neg value: -inf


In [13]:
X_test_save_path = os.path.join(
    DATAPATH, "feature_extraction/spectral_analysis_X_test_features.csv"
)
test_features.to_csv(X_test_save_path, index=True)